# Introdução a Multi-Armed e Contextual Bandit

## Índice
1. [Introdução](#Introdução)
2. [Problemas Multi-Armed Bandit](#Problemas-Multi-Armed-Bandit)
3. [Contextual Bandit](#Contextual-Bandit)
4. [Conclusão](#Conclusão)
5. [Referências](#Referências)

## Introdução

Este documento apresenta uma breve discussão sobre algoritmos Contextual Bandit. Inicio introduzindo problemas do tipo Multi-Armed Bandit e o dilema Exploration-Exploitaition, incluindo implementação e validação de alguns algoritmos de solução aproximada ao problema.

Na seção seguinte demonstro como problemas Multi-Armed Bandit se relacionam com Contextual Bandits e apresento um comparativo de desempenho entre as soluções.


## Problemas Multi-Armed Bandit

### Contexto

<img src="https://cdn-images-1.medium.com/max/1600/0*IMcXHTPn28t4ddWX." width=1544 height=600>


Imagine que você é um apostador em um cassino e deseja maximizar seus lucros jogando em máquinas caça-níquel, também conhecidas como 'one-armed bandit', por conta da alavanca e da propensão a levar todo o dinheiro dos apostadores. Vamos considerar uma máquina caça-níquel com várias alavancas, cada uma com probabilidade $P_i$ de premiar o apostador, com valor de premiação fixo. Para conseguirmos o maior ganho possível, bastaria escolher alavanca cujo $P_i$ é máximo.

O problema é que não conhecemos previamente os parâmetros que definem as alavancas. Portanto, precisamos coletar dados antes de concluir qual é a alavanca mais lucrativa.

Uma possível solução seria executar um teste AB, de forma a estabelecer estimativas suficientemente confiáveis dos parâmetros de todas as alavancas de maneira que, ao final do experimento, possamos determinar qual é a melhor. Essa abordagem, embora válida, possui algumas limitações:

- O teste AB é extremamente custoso. Como o experimento consiste em coletar dados uniformemente de todas as alavancas, mesmo que em algum ponto já tivéssemos informação suficiente para escolher a melhor, o teste continuará selecionando da mesma maneira alavancas piores até que o teste seja encerrado.
- O teste AB é estático. Ele funciona bem para o caso em que as alavancas não se alteram ao longo do tempo. Em cenários dinâmicos, cada vez que uma nova alavanca surge, teríamos de propor um novo teste.

<img src="https://conversionxl.com/wp-content/uploads/2015/09/abtesting-conversion-xl.jpg" width=568 height=405>

O teste AB ilustra bem o dilema Exploration-Exploitation. Num primeiro momento, enquanto o experimento está em execução, o sistema é 100% Exploration, ou seja, escolhe aleatoriamente as alavancas, maximizando o aprendizado. Por outro lado, isso faz com que escolhas não-ótimas sejam realizadas durante um período muito longo, tornando-o excesivamente custoso. Após o final do experimento observa-se o inverso, o sistema se torna 100% Exploitation, maximizando os ganhos. Somente a alavanca vencedora passa a ser escolhida e o sistema para de aprender, sendo necessário realizar um novo teste AB para escolher um novo vencedor.

<img src="https://conversionxl.com/wp-content/uploads/2015/09/Screen-Shot-2015-09-04-at-4.12.27-PM-1.jpg" width=568 height=405>

Propostas de soluções para Multi-Armed Bandit focam em equilibrar a questão Exploration-Exploitation, balanceando aprendizado e ganhos ao longo da execução.


### Definição

De maneira mais formal, um problema Multi-Armed Bandit é definido pela existência de um **agente** (apostador) que pode executar um conjunto de **ações** (escolher e puxar alavancas). Cada **ação** possui uma distribuição probabilística de **recompensas** (chance de ser premiado) associada, independente das demais. A cada **turno** (cada aposta), o agente escolhe uma das ações para executar, tendo acesso somente às informações de número de turnos executados, ações escolhidas e respectivas recompensas. O agente não tem acesso às recompensas de escolhas que não foram feitas e considera-se que as ações não alteram as distribuições de recomensas.

O objetivo é minimizar o **arrependimento** (regret) do processo em um número finito de turnos, que é a diferença dos ganhos entre as escolhas realizadas e a expectativa da escolha ótima no período do experimento.

O processo descrito é resumido na seguinte imagem:

<img src="img/multi-armed-bandit-definition.png" width=568 height=405>

Embora a princípio um pouco abstrato, diversos problemas cotidianos podem ser modelados como problemas Multi-Armed Bandit, como por exemplo:

- Recomendação de conteúdo, como notícias ou propagandas
- Roteamento de redes
- Ensaios clínicos

A seguir, apresento algumas das soluções aproximadas para o problema.


### Soluções

#### Explore Then Exploit

A primeira proposta é, em sua essência, um teste AB. Primeiro é executada uma etapa de descoberta de $N$ rodadas em que o agente tenta encontrar a melhor solução. Desse ponto em diante, o agente escolhe somente a alavanca de maior expectativa de ganhos.

Abaixo, é demonstrada uma simulação com diferentes valores de N para um problema com 9 alavancas:

In [1]:
import numpy as np
import pandas as pd
import plotly.offline as pyo
import plotly.graph_objs as go

from src.ExploreThenExploit import ExploreThenExploit
from src.OneArmedBandit import OneArmedBandit

pyo.init_notebook_mode(connected=True)

bandits = [OneArmedBandit(i * 0.05 + 0.35) for i in range(9)]
alg = ExploreThenExploit(bandits)
traces = []

for i in range(5):
    alg.run_experiment(n_exploration_rounds=50 * (2 ** i), experiment_length=5000, seed=42)
    s = pd.Series(alg.experiment_rewards)
    s = s.expanding().mean()
    traces.append(
        go.Scatter(
          x=list(range(5000)),
          y=s,
          name='N = ' + str(50 * (2 ** i))
        )
    )
    
layout = go.Layout(
    title='Ganho médio acumulado por período de Exploration',
    xaxis=dict(title='Número de rodadas'),
    yaxis=dict(title='Ganho médio acumulado'),
    shapes=[
        dict(
            type='line',
            x0=0,
            y0=0.75,
            x1=5000,
            y1=0.75,
            line=dict(
                dash='dash'
            )
        )
    ]
)

fig = go.Figure(data=traces, layout=layout)

pyo.iplot(fig)

O gráfico acima demonstra de forma clara as limitações dessa abordagem. Para os casos em que N é muito pequeno (nessa simulação, N < 400), o agente pode não convergir para a solução correta por força do acaso. Já quando N é muito grande, o ganho nas rodadas iniciais é muito menor do que o esperado no caso da escolha da melhor solução, e o prejuízo inicial precisa de um número maior de rodadas para ser diluído.

#### Epsilon-Greedy

Outra possível solução é dada pelo algoritmo Epsilon-Greedy. A grande diferença está na existência do parâmetro $\epsilon$, que determina a chance do agente realizar Exploration. No restante das rodadas o agente realiza Exploitation com base na melhor alavanca até aquele momento. A figura a seguir ilustra esse processo:

<img src="https://imaddabbura.github.io/img/bandit_algorithms/epsilon_greedy.PNG" width=568 height=405>

Novamente demonstramos uma simulação com diferentes valores de $\epsilon$ para um problema com 9 alavancas:

In [2]:
from src.EpsilonGreedy import EpsilonGreedy
from src.OneArmedBandit import OneArmedBandit

bandits = [OneArmedBandit(i * 0.05 + 0.35) for i in range(9)]
alg = EpsilonGreedy(bandits)
traces = []

for i in range(5):
    alg.run_experiment(epsilon=0.05 * (i + 1), experiment_length=5000, seed=42)
    s = pd.Series(alg.experiment_rewards)
    s = s.expanding().mean()
    traces.append(
        go.Scatter(
          x=list(range(5000)),
          y=s,
          name=f'Epsilon = {0.05 * (i + 1):1.2f}'
        )
    )
    
layout = go.Layout(
    title='Ganho médio acumulado por epsilon',
    xaxis=dict(title='Número de rodadas'),
    yaxis=dict(title='Ganho médio acumulado'),
    shapes=[
        dict(
            type='line',
            x0=0,
            y0=0.75,
            x1=5000,
            y1=0.75,
            line=dict(
                dash='dash'
            )
        )
    ]
)

fig = go.Figure(data=traces, layout=layout)

pyo.iplot(fig)

In [3]:
alg.run_experiment(epsilon=0.1, experiment_length=5000, seed=42)

traces = [go.Scatter(
    x=list(range(5000)),
    y=alg.experiment_bandits_selected,
    name=f'Epsilon = {0.05 * (i + 1):1.2f}',
    mode='markers'
)]

layout = go.Layout(
    title='Ativações de alavanca por rodada',
    xaxis=dict(title='Número de rodadas'),
    yaxis=dict(title='Alavanca')
)

fig = go.Figure(data=traces, layout=layout)

pyo.iplot(fig)

Podemos observar que o Epsilon-Greedy (com $\epsilon = 0.1$) converge rapidamente para a segunda melhor solução e após aproximadamente 300 iterações seleciona a melhor alavanca. É interessante notar que após algumas milhares de iterações na simulação, o teste AB supera o Epsilon-Greedy, pois após a etapa inicial de Exploration ele toma decisões de Exploitation, enquanto o Epsilon-Greedy mantém uma proporção de Exploration-Exploitation fixa. Concluímos então que o Epsilon-Greedy tem como principais vantagens em relação ao teste AB:

1. Convergir mais rápido para uma solução boa ou ótima
2. Risco menor de convergir para uma solução ruim
3. Ser adaptável. Mesmo que a configuração das alavancas mude, ainda assim o agente seria capaz de continuar aprendendo, pois sempre há Exploration (OBS: para esse cenário seria interessante incluir uma adaptação no algoritmo, como decaimento no tempo, de forma a não "engessar" as estimativas).



## Contextual Bandit

Uma das limitações de problemas (e soluções) Multi-Armed Bandit clássicos é que considera-se que o agente só possui acesso às informações por ele coletadas, desconsiderando informações externas do ambiente. Soluções Contextual Bandit expandem as Multi-Armed Bandit incluindo no processo de decisão, além do histórico de ações e recompensas, um vetor de features (como em problemas de aprendizado supervisionado), que assume-se ter algum tipo de associação com a recompensa.

<img src="https://cdn-images-1.medium.com/max/1600/1*HH9PGI9dThtu6BpJtLmABg.png" width=568 height=405>

Tem-se assim uma solução que, ao invés de convergir para a alavanca mais popular, encontra a melhor alavanca para cada caso, dando uma resposta personalizada. Os casos de uso são os mesmos dos Multi-Armed Bandit, com destaque para casos em que há muita informação disponível sobre quem gera a recompensa, como recomendações de produtos/serviços ou exibição de conteúdo e anúncios.

No artigo [Adapting multi-armed bandits policies to contextual bandits scenarios](https://arxiv.org/pdf/1811.04383.pdf), o autor adapta uma série de soluções Multi-Armed para Contextual. A principal modificação é a introdução de modelos de aprendizado supervisionados no lugar da utilização de estimativas de média sobre o histórico.


### Soluções

#### Epsilon-Greedy (novamente!)

As soluções com e sem contexto são essencialmente as mesmas, tendo como única diferença o critério que determina qual é a melhor alavanca em uma rodada, em que a solução com contexto usa um histórico de características como em um problema de aprendizado supervisionado. Além disso, a implementação escolhida inclui algumas outras modificações em relação ao algoritmo clássico:

- decay: fator de decaimento de $\epsilon$. Conforme as rodadas vão sendo executadas, a probabilidade de Exploration diminui. Quando decay = 1, não há decaimento.
- beta_prior: no início do experimento, quando há poucas amostras para cada alavanca, utiliza-se de um sorteio para escolher a alavanca, sem uso do contexto.
- smoothing: Atribui pesos às previsões dos modelos supervisionados com base no número de amostras vistas. Tem o mesmo objetivo do beta_prior, evitar problemas de cold start.

#### Bootstraped Upper Confidence Bound

Uma outra família de soluções Multi-Armed é a Upper Confidence Bound (UCB). Seu princípio é o do "otimismo em face da incerteza". A alavanca escolhida é a que apresenta a maior possibilidade de recompensa, dado um limite superior calculado. Conforme mais informação é adquirida sobre uma alavanca, a distância entre a sua média e o limite superior vai reduzindo, o que significa que eventualmente o UCB converge para a melhor alavanca.

O bootstrapped vem da reamostragem realizada para alimentar o treinamento de cada modelo supervisionado.

A seguir, demonstro as duas soluções através da implementação para Python [contextualbandits](https://www.github.com/david-cortes/contextualbandits/), usando o dataset [Bibtex](http://manikvarma.org/downloads/XC/XMLRepository.html). A maior parte do código abaixo foi adaptada do notebook de demonstração [Online Contextual Bandits](https://nbviewer.jupyter.org/github/david-cortes/contextualbandits/blob/master/example/online_contextual_bandits.ipynb).


In [4]:
import pandas as pd, numpy as np, re
from sklearn.preprocessing import MultiLabelBinarizer

def parse_data(file_name):
    features = list()
    labels = list()
    with open(file_name, 'rt') as f:
        f.readline()
        for l in f:
            if bool(re.search("^[0-9]", l)):
                g = re.search("^(([0-9]{1,2},?)+)\s(.*)$", l)
                labels.append([int(i) for i in g.group(1).split(",")])
                features.append(eval("{" + re.sub("\s", ",", g.group(3)) + "}"))
            else:
                l = l.strip()
                labels.append([])
                features.append(eval("{" + re.sub("\s", ",", l) + "}"))
    features = pd.DataFrame.from_dict(features).fillna(0).values
    mlb = MultiLabelBinarizer()
    y = mlb.fit_transform(labels)
    return features, y

X, y = parse_data("data/Bibtex_data.txt")

In [5]:
from sklearn.linear_model import LogisticRegression
from contextualbandits.online import BootstrappedUCB, EpsilonGreedy
from copy import deepcopy

nchoices = y.shape[1]
base_algorithm = LogisticRegression(random_state=42, solver='lbfgs')
beta_prior = ((3, 7), 2) # until there are at least 2 observations of each class, will use prior Beta(3, 7)

## The base algorithm is embedded in different metaheuristics
bootstrapped_ucb = BootstrappedUCB(deepcopy(base_algorithm), nchoices = nchoices, beta_prior=beta_prior)
epsilon_greedy = EpsilonGreedy(deepcopy(base_algorithm), nchoices = nchoices, beta_prior=beta_prior)

models = [bootstrapped_ucb, epsilon_greedy]


# These lists will keep track of the rewards obtained by each policy
rewards_ucb, rewards_egr = [[] for i in range(len(models))]

lst_rewards = [rewards_ucb, rewards_egr]

# batch size - algorithms will be refit after N rounds
batch_size=50

# initial seed - all policies start with the same small random selection of actions/rewards
first_batch = X[:batch_size, :]
action_chosen = np.random.randint(nchoices, size=batch_size)
rewards_received = y[np.arange(batch_size), action_chosen]

# fitting models for the first time
for model in models:
    np.random.seed(123)
    model.fit(X=first_batch, a=action_chosen, r=rewards_received)
    
# these lists will keep track of which actions does each policy choose
lst_a_ucb, lst_a_egr = [action_chosen.copy() for i in range(len(models))]

lst_actions = [lst_a_ucb, lst_a_egr]

# rounds are simulated from the full dataset
def simulate_rounds(model, rewards, actions_hist, X_global, y_global, batch_st, batch_end):
    np.random.seed(batch_st)
    
    ## choosing actions for this batch
    actions_this_batch = model.predict(X_global[batch_st:batch_end, :]).astype('uint8')
    
    # keeping track of the sum of rewards received
    rewards.append(y_global[np.arange(batch_st, batch_end), actions_this_batch].sum())
    
    # adding this batch to the history of selected actions
    new_actions_hist = np.append(actions_hist, actions_this_batch)
    
    # now refitting the algorithms after observing these new rewards
    np.random.seed(batch_st)
    model.fit(X_global[:batch_end, :], new_actions_hist, y_global[np.arange(batch_end), new_actions_hist])
    
    return new_actions_hist

# now running all the simulation
for i in range(int(np.floor(X.shape[0] / batch_size))):
    batch_st = (i + 1) * batch_size
    batch_end = (i + 2) * batch_size
    batch_end = np.min([batch_end, X.shape[0]])
    
    for model in range(len(models)):
        lst_actions[model] = simulate_rounds(models[model],
                                             lst_rewards[model],
                                             lst_actions[model],
                                             X, y,
                                             batch_st, batch_end)


In [6]:
def get_mean_reward(reward_lst, batch_size=batch_size):
    mean_rew=list()
    for r in range(len(reward_lst)):
        mean_rew.append(sum(reward_lst[:r+1])/((r+1)*batch_size))
    return mean_rew

traces = [
    go.Scatter(
        x=list(range(0, len(rewards_egr) * 50, 50)),
        y=get_mean_reward(rewards_egr),
        name='Epsilon-Greedy'
    ),
    go.Scatter(
        x=list(range(0, len(rewards_egr) * 50, 50)),
        y=get_mean_reward(rewards_ucb),
        name='Bootstrapped UCB'
    ),
    go.Scatter(
        x=list(range(0, len(rewards_egr) * 50, 50)),
        y=np.repeat(y.mean(axis=0).max(),len(rewards_ucb)),
        name='Melhor alavanca (sem contexto)',
        line=dict(dash='dash')
    ),
    
]

layout = go.Layout(
    title='Comparativo de ganhos médios acumulados de soluções Contextual',
    xaxis=dict(title='Número de rodadas (modelos atualizados a cada 50 rodadas)'),
    yaxis=dict(title='Ganho médio acumulado')
)

fig = go.Figure(data=traces, layout=layout)

pyo.iplot(fig)


O gráfico acima deixa evidente os benefícios de soluções que se utilizam de contexto. Ambos os algoritmos superaram a escolha da melhor alavanca no caso sem contexto, que é o limite teórico de ganhos de soluções Multi-Armed.

Um problema observado é o tempo de execução dos experimentos. Como após cada batch de N rodadas o modelo supervisionado precisa ser retreinado utilizando todos os dados observados, o tempo de treinamento explode rapidamente. Uma possível solução seria atualizar os modelos em menor frequência, o que provavelmente resultaria em menor ganho ou usar um modelo supervisionado que permita online learning, assim o dataset de treinamento sempre seria limitado ao tamanho do batch.

## Conclusão

Neste estudo, vimos o que são problemas Multi-Armed Bandit, algumas possíveis soluções e como elas podem ser expandidas para Contextual Bandit, que apresentam desempenho muito superior, embora em troca requeiram muito mais recursos computacionais.

O estudo poderia ser aprofundado com a análise de outros algoritmos, como o LinUCB e suas variações, bem como outras implementações dos algoritmos testados. Também seria interessante verificar quais soluções seriam viáveis num ambiente real e até que ponto elas são escaláveis.

## Referências

Lista de artigos, papers, livros e repositórios consultados para a elaboração deste documento.

- [Wikipedia - Multi-Armed Bandit](https://en.wikipedia.org/wiki/Multi-armed_bandit)
- [Optimizely - Multi-Armed Bandit](https://www.optimizely.com/optimization-glossary/multi-armed-bandit/)
- [CXL - When to Run Bandit Tests Instead of A/B/n Tests](https://conversionxl.com/blog/bandit-tests/)
- [Analytics Vidihya - Reinforcement Learning Guide: Solving the Multi-Armed Bandit Problem from Scratch in Python](https://www.analyticsvidhya.com/blog/2018/09/reinforcement-multi-armed-bandit-scratch-python/)
- [Google Analytics - Multi-armed bandit experiments](https://support.google.com/analytics/answer/2844870?hl=en)
- [Medium - Solving multiarmed bandits: A comparison of epsilon-greedy and Thompson sampling](https://towardsdatascience.com/solving-multiarmed-bandits-a-comparison-of-epsilon-greedy-and-thompson-sampling-d97167ca9a50)
- [Lil'Log - The Multi-Armed Bandit Problem and Its Solutions](https://lilianweng.github.io/lil-log/2018/01/23/the-multi-armed-bandit-problem-and-its-solutions.html)
- [Math ∩ Programming - Optimism in the Face of Uncertainty: the UCB1 Algorithm](https://jeremykun.com/2013/10/28/optimism-in-the-face-of-uncertainty-the-ucb1-algorithm/)
- [Kuleshov, V., & Precup, D. (2014).  Algorithms for the multi-armed bandit problem. arXiv:1402.6028 [cs.AI]](https://arxiv.org/abs/1402.6028)
- [Medium - Contextual Bandits and Reinforcement Learning](https://towardsdatascience.com/contextual-bandits-and-reinforcement-learning-6bdfeaece72a)
- [stream - An Introduction to Contextual Bandits](https://getstream.io/blog/introduction-contextual-bandits/)
- [Joh Maxwell - Contextual Bandits: LinUCB](http://john-maxwell.com/post/2017-03-17/)
- [Li, L., Chu, W., Langford, J., & Schapire, R. E. (2010, April). A contextual-bandit approach to personalized news article recommendation.](http://rob.schapire.net/papers/www10.pdf)
- [Cortes, D. (2018). Adapting multi-armed bandits policies to contextual bandits scenarios. arXiv preprint arXiv:1811.04383.](https://arxiv.org/pdf/1811.04383.pdf)
- [GitHub - contextualbandits](https://github.com/david-cortes/contextualbandits)
- [Tor Lattimore, T. & Szepesvári, C. (2018). Bandit Algorithms. Cambridge University Press (draft)](http://downloads.tor-lattimore.com/banditbook/book.pdf)

